In [2]:
import pandas as pd
import numpy as np
import folium
from ast import literal_eval
import re
import requests
from random import randint, shuffle
#import json

## user 파일 불러오기, 샘플링

In [7]:
#user_id_map 불러오기 
user = pd.read_csv('user_id_map.csv')
user.shape

(876145, 2)

In [8]:
#10000명 샘플링
user_1 = user.iloc[1,:] #id=1 추가
user = user.sample(n=10000)
user = user.sort_values(by='user_id_csv').reset_index(drop=True) 
user.iloc[0,:] = user_1
user.head()

user_id_csv                           user_id
0            1  72fb0d0087d28c832f15776b0d936598
1          163  854c0f8798c2d694255830bb6ea29416
2          293  9d10196759e6bedd378367a12f639fc1
3          449  515ce9e61827255a3569b93635d00773
4          663  0a42d0d0e55ef8ec8de411e1baec6880

In [9]:
user.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   user_id_csv  10000 non-null  int64 
 1   user_id      10000 non-null  object
dtypes: int64(1), object(1)
memory usage: 156.4+ KB


## id, pw, email, nickname 생성

In [10]:
#id unique한지 확인
user.shape[0], user['user_id_csv'].nunique(), user['user_id'].nunique()

(10000, 10000, 10000)

In [11]:
# 닉네임 리스트 불러오기
url = 'https://svnweb.freebsd.org/csrg/share/dict/propernames?revision=61766&view=co'
r = requests.get(url)
names = r.text.split()
shuffle(names) #알파벳 순 -> random shuffling
print(len(names)) #1323개

1323


In [12]:
user['id'] = user['user_id_csv']
user['pw'] = user['user_id_csv']
user['email'] = user['user_id'].apply(lambda x: x[:8] + '@bkms.com') #user_id 0-7번째 글자를 메일 아이디로!
user['nickname'] = user['id'].apply(lambda x: names[x % len(names)]+str(x)[:4])

In [13]:
user.head()

user_id_csv                           user_id   id   pw              email  \
0            1  72fb0d0087d28c832f15776b0d936598    1    1  72fb0d00@bkms.com   
1          163  854c0f8798c2d694255830bb6ea29416  163  163  854c0f87@bkms.com   
2          293  9d10196759e6bedd378367a12f639fc1  293  293  9d101967@bkms.com   
3          449  515ce9e61827255a3569b93635d00773  449  449  515ce9e6@bkms.com   
4          663  0a42d0d0e55ef8ec8de411e1baec6880  663  663  0a42d0d0@bkms.com   

     nickname  
0     Judith1  
1  Dimetry163  
2    Jarmo293  
3   Graham449  
4   Donnie663

In [15]:
user.nickname.nunique(), user.email.nunique() #닉네임, 이메일 모두 unique!

(9999, 10000)

## 주소 데이터 전처리 및 확인

In [ ]:
'''
apt = pd.read_csv(dir+'seoul_latlong.csv', index_col=0)
def latlong_to_float(x):
  try:
    return float(x)
  except:
    return None
apt['위도'] = apt['위도'].apply(lambda x: latlong_to_float(x))
apt['경도'] = apt['경도'].apply(lambda x: latlong_to_float(x))
apt['address_gu'] = apt['주소'].apply(lambda x: x.split(' ')[1])
apt['address_dong'] = apt['주소'].apply(lambda x: x.split(' ')[2])
apt.columns = ['address', 'lat_long', 'lat', 'long', 'address_gu', 'address_dong']
apt = apt[['address', 'address_gu', 'address_dong', 'lat_long', 'lat', 'long']].dropna()
apt.to_csv(dir+'seoul_address.csv', index=False)
'''
# 구, 동 추출
# 알맞은 data type로 전환
# 위도, 경도 invalid 값 제거
# seoul_address.csv에 저장

"\napt = pd.read_csv(dir+'seoul_latlong.csv', index_col=0)\ndef latlong_to_float(x):\n  try:\n    return float(x)\n  except:\n    return None\napt['위도'] = apt['위도'].apply(lambda x: latlong_to_float(x))\napt['경도'] = apt['경도'].apply(lambda x: latlong_to_float(x))\napt['address_gu'] = apt['주소'].apply(lambda x: x.split(' ')[1])\napt['address_dong'] = apt['주소'].apply(lambda x: x.split(' ')[2])\napt.columns = ['address', 'lat_long', 'lat', 'long', 'address_gu', 'address_dong']\napt = apt[['address', 'address_gu', 'address_dong', 'lat_long', 'lat', 'long']].dropna()\napt.to_csv(dir+'seoul_address.csv', index=False)\n"

In [16]:
apt = pd.read_csv('seoul_address.csv', converters={'lat_long': pd.eval})
apt.head()

address address_gu address_dong  \
0           서울특별시 금천구 시흥동 시흥성지        금천구          시흥동   
1       서울특별시 강남구 도곡동 도곡1차아이파크        강남구          도곡동   
2   서울특별시 양천구 신정동 신정대성유니드아파트2차        양천구          신정동   
3  서울특별시 노원구 중계동 중계라이프신동아청구아파트        노원구          중계동   
4      서울특별시 노원구 하계동 하계2차현대아파트        노원구          하계동   

                               lat_long        lat        long  
0  [37.4541515451134, 126.908853793235]  37.454152  126.908854  
1  [37.4922748332904, 127.043511837517]  37.492275  127.043512  
2  [37.5210153975411, 126.848911008994]  37.521015  126.848911  
3  [37.6519317309728, 127.079543228581]  37.651932  127.079543  
4  [37.6446075819338, 127.072058758551]  37.644608  127.072059

In [17]:
apt.info() #2746개

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2746 entries, 0 to 2745
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   address       2746 non-null   object 
 1   address_gu    2746 non-null   object 
 2   address_dong  2746 non-null   object 
 3   lat_long      2746 non-null   object 
 4   lat           2746 non-null   float64
 5   long          2746 non-null   float64
dtypes: float64(2), object(4)
memory usage: 128.8+ KB


In [18]:
apt[apt['address'].duplicated()]
apt[apt['address'] == apt.iloc[1630,0]] # 근데 위도, 경도는 다르니까 킵하겠음

address address_gu address_dong  \
1164  서울특별시 양천구 목동 목동성원        양천구           목동   
1630  서울특별시 양천구 목동 목동성원        양천구           목동   

                                  lat_long        lat        long  
1164  [37.5358479839678, 126.869907138224]  37.535848  126.869907  
1630  [37.5263981035576, 126.869331996718]  37.526398  126.869332

In [19]:
m = folium.Map(location=apt.iloc[0,3],
               zoom_start=12, 
               width=750, 
               height=500)
folium.Marker(apt.iloc[0,3],
              tooltip=apt.iloc[0,0],
              popup = '0').add_to(m)
m

## 주소 랜덤 생성

In [20]:
# lat, long에 랜덤 넣기 (노이즈 N(0,0.01)로 추가)
n = user.shape[0] // apt.shape[0]
newdf = pd.DataFrame(np.repeat(apt.values, n+1, axis=0))
newdf.columns = apt.columns
for i in range(newdf.shape[0]):
  if i% n !=0:
    # 노이즈 추가
    newdf.iloc[i,4] = newdf.iloc[i,4] + np.random.uniform(0,0.001)
    newdf.iloc[i,5] = newdf.iloc[i,5] + np.random.uniform(0,0.001)
newdf['lat_long'] = newdf[['lat','long']].values.tolist()
newdf = newdf.sample(n = user.shape[0]).reset_index(drop=True)
newdf.head()

address address_gu address_dong  \
0         서울특별시 강남구 도곡동 도곡대림        강남구          도곡동   
1    서울특별시 동작구 상도동 상도래미안1차제2        동작구          상도동   
2  서울특별시 성동구 금호동4가 서울숲2차푸르지오        성동구        금호동4가   
3  서울특별시 은평구 구산동 갈현1단지e-편한세상        은평구          구산동   
4   서울특별시 영등포구 문래동3가 문래자이아파트       영등포구        문래동3가   

                                  lat_long        lat        long  
0     [37.4865450724295, 127.039889051865]  37.486545  127.039889  
1  [37.50571609361137, 126.93334302462937]  37.505716  126.933343  
2     [37.5461200187428, 127.024069426318]   37.54612  127.024069  
3  [37.61222070967136, 126.90719433978998]  37.612221  126.907194  
4  [37.51634929893328, 126.89697455210819]  37.516349  126.896975

In [22]:
newuser = pd.concat([user,newdf],axis=1)
newuser.head()

user_id_csv                           user_id   id   pw              email  \
0            1  72fb0d0087d28c832f15776b0d936598    1    1  72fb0d00@bkms.com   
1          163  854c0f8798c2d694255830bb6ea29416  163  163  854c0f87@bkms.com   
2          293  9d10196759e6bedd378367a12f639fc1  293  293  9d101967@bkms.com   
3          449  515ce9e61827255a3569b93635d00773  449  449  515ce9e6@bkms.com   
4          663  0a42d0d0e55ef8ec8de411e1baec6880  663  663  0a42d0d0@bkms.com   

     nickname                    address address_gu address_dong  \
0     Judith1         서울특별시 강남구 도곡동 도곡대림        강남구          도곡동   
1  Dimetry163    서울특별시 동작구 상도동 상도래미안1차제2        동작구          상도동   
2    Jarmo293  서울특별시 성동구 금호동4가 서울숲2차푸르지오        성동구        금호동4가   
3   Graham449  서울특별시 은평구 구산동 갈현1단지e-편한세상        은평구          구산동   
4   Donnie663   서울특별시 영등포구 문래동3가 문래자이아파트       영등포구        문래동3가   

                                  lat_long        lat        long  
0     [37.4865450724295, 127.039889051865]  37.486545  127.039889  
1  [37.50571609361137, 126.93334302462937]  37.505716  126.933343  
2     [37.5461200187428, 127.024069426318]   37.54612  127.024069  
3  [37.61222070967136, 126.90719433978998]  37.612221  126.907194  
4  [37.51634929893328, 126.89697455210819]  37.516349  126.896975

In [23]:
m = folium.Map(location=newuser.iloc[0,9],
               zoom_start=15, 
               width=750, 
               height=500)
folium.Marker(newuser.iloc[0,9],
              tooltip=newuser.iloc[0,5],
              popup = f'id: {newuser.iloc[0,0]}, nickname:{newuser.iloc[0,5]}, email: {newuser.iloc[0,4]}\naddress: {newuser.iloc[0,6]}').add_to(m)
m #도곡동 맞게 나옴

In [38]:
# 유저 분포 살펴보기
m = folium.Map(location=[37.516119, 126.975832],
               zoom_start=10.8, 
               width=750, 
               height=500)
for index, row in newuser.iterrows():
    folium.CircleMarker(location=row[9]).add_to(m)
m

In [25]:
newuser.to_csv('users.csv', index=False)

In [26]:
#import pandas as pd
u = pd.read_csv('users.csv')
u.head()

user_id_csv                           user_id   id   pw              email  \
0            1  72fb0d0087d28c832f15776b0d936598    1    1  72fb0d00@bkms.com   
1          163  854c0f8798c2d694255830bb6ea29416  163  163  854c0f87@bkms.com   
2          293  9d10196759e6bedd378367a12f639fc1  293  293  9d101967@bkms.com   
3          449  515ce9e61827255a3569b93635d00773  449  449  515ce9e6@bkms.com   
4          663  0a42d0d0e55ef8ec8de411e1baec6880  663  663  0a42d0d0@bkms.com   

     nickname                    address address_gu address_dong  \
0     Judith1         서울특별시 강남구 도곡동 도곡대림        강남구          도곡동   
1  Dimetry163    서울특별시 동작구 상도동 상도래미안1차제2        동작구          상도동   
2    Jarmo293  서울특별시 성동구 금호동4가 서울숲2차푸르지오        성동구        금호동4가   
3   Graham449  서울특별시 은평구 구산동 갈현1단지e-편한세상        은평구          구산동   
4   Donnie663   서울특별시 영등포구 문래동3가 문래자이아파트       영등포구        문래동3가   

                                  lat_long        lat        long  
0     [37.4865450724295, 127.039889051865]  37.486545  127.039889  
1  [37.50571609361137, 126.93334302462937]  37.505716  126.933343  
2     [37.5461200187428, 127.024069426318]  37.546120  127.024069  
3  [37.61222070967136, 126.90719433978998]  37.612221  126.907194  
4  [37.51634929893328, 126.89697455210819]  37.516349  126.896975

In [27]:
u.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 12 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   user_id_csv   10000 non-null  int64  
 1   user_id       10000 non-null  object 
 2   id            10000 non-null  int64  
 3   pw            10000 non-null  int64  
 4   email         10000 non-null  object 
 5   nickname      10000 non-null  object 
 6   address       10000 non-null  object 
 7   address_gu    10000 non-null  object 
 8   address_dong  10000 non-null  object 
 9   lat_long      10000 non-null  object 
 10  lat           10000 non-null  float64
 11  long          10000 non-null  float64
dtypes: float64(2), int64(3), object(7)
memory usage: 937.6+ KB
